# 1. Setup Mario


In [1]:
!pip install gym_super_mario_bros==7.3.0 nes_py



[notice] A new release of pip is available: 23.0.1 -> 23.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [1]:
# Import the game
import gym_super_mario_bros
# Import the Joypad wrapper
from nes_py.wrappers import JoypadSpace
# Import the SIMPLIFIED controls
from gym_super_mario_bros.actions import SIMPLE_MOVEMENT

In [2]:
# Setup game
env = gym_super_mario_bros.make('SuperMarioBros-v1')
env = JoypadSpace(env, SIMPLE_MOVEMENT)

In [3]:
env.observation_space.shape #pixiel diminsions, so what we get back from the game


(240, 256, 3)

In [4]:
# Create a flag - restart or not
done = True
# Loop through each frame in the game
for step in range(100000): 
    # Start the game to begin with 
    if done: 
        # Start the gamee
        env.reset()
    # Do random actions
    state, reward, done, info = env.step(env.action_space.sample())
    # Show the game on the screen
    env.render()
# Close the game
env.close()

C:\Users\16132\Documents\ML-mario\myenv\lib\site-packages\pyglet\image\codecs\wic.py:289: UserWarning: [WinError -2147417850] Cannot change thread mode after it is set
  warnings.warn(str(err))
C:\Users\16132\Documents\ML-mario\myenv\lib\site-packages\gym_super_mario_bros\smb_env.py:148: RuntimeWarning: overflow encountered in scalar subtract
  return (self.ram[0x86] - self.ram[0x071c]) % 256


KeyboardInterrupt: 

In [5]:
env.close()

# 2. Preprocess Environment


In [60]:
!pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu117

Looking in indexes: https://download.pytorch.org/whl/cu117


[notice] A new release of pip available: 22.3.1 -> 23.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [16]:
# Install stable baselines for RL stuff
!pip install stable-baselines3[extra]


[notice] A new release of pip available: 22.3.1 -> 23.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [6]:
# Import Frame Stacker Wrapper and GrayScaling Wrapper
from gym.wrappers import GrayScaleObservation
# Import Vectorization Wrappers
from stable_baselines3.common.vec_env import VecFrameStack, DummyVecEnv
# Import Matplotlib to show the impact of frame stacking
from matplotlib import pyplot as plt

In [7]:
# 1. Create the base environment
env = gym_super_mario_bros.make('SuperMarioBros-v0')
# 2. Simplify the controls 
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale, cuts down amount of data, as color data costs more, need to consider blue, red, green. Need to deal with only a third of the data now
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environment
env = DummyVecEnv([lambda: env])
# 5. Stack the frames: when frame stacking you get access not just to the current frame, but the most recent frames as well
env = VecFrameStack(env, 4, channels_order='last')

In [8]:
state = env.reset()

In [9]:
state.shape

(1, 240, 256, 4)

In [28]:
state, reward, done, info = env.step([5])# the [5] is the 5th possible control, which is jump


# 3. Train the RL Model


In [10]:
# Import os for file path management
import os 
# Import PPO for algos
from stable_baselines3 import PPO
# Import Base Callback for saving models
from stable_baselines3.common.callbacks import BaseCallback

In [11]:
class TrainAndLoggingCallback(BaseCallback):

    def __init__(self, check_freq, save_path, verbose=1):
        super(TrainAndLoggingCallback, self).__init__(verbose)
        self.check_freq = check_freq
        self.save_path = save_path

    def _init_callback(self):
        if self.save_path is not None:
            os.makedirs(self.save_path, exist_ok=True)

    def _on_step(self):
        if self.n_calls % self.check_freq == 0:
            model_path = self.save_path +"\\Best_Model"
            print(model_path)
            self.model.save(model_path)

        return True

In [12]:
CHECKPOINT_DIR = 'C:/Users/16132/Documents/ML-mario/Training/saved_models/'
LOG_DIR = 'C:/Users/16132/Documents/ML-mario/Training/logs/'

In [13]:
callback = TrainAndLoggingCallback(check_freq=10000, save_path=CHECKPOINT_DIR)

In [14]:
# This is the AI model started
model = PPO('CnnPolicy', env, verbose=1, tensorboard_log=LOG_DIR, learning_rate=0.000001, 
            n_steps=512) 

Using cuda device
Wrapping the env in a VecTransposeImage.


In [42]:
model.learn(total_timesteps=1000000, callback=callback)

Logging to C:/Users/16132/Documents/ML-mario/Training/logs/PPO_2
----------------------------
| time/              |     |
|    fps             | 149 |
|    iterations      | 1   |
|    time_elapsed    | 3   |
|    total_timesteps | 512 |
----------------------------
-------------------------------------------
| time/                   |               |
|    fps                  | 80            |
|    iterations           | 2             |
|    time_elapsed         | 12            |
|    total_timesteps      | 1024          |
| train/                  |               |
|    approx_kl            | 1.4302437e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.95         |
|    explained_variance   | 0.00103       |
|    learning_rate        | 1e-06         |
|    loss                 | 201           |
|    n_updates            | 10            |
|    policy_gradient_loss | -0.000225     |
|    value_loss           | 

KeyboardInterrupt: 

In [ ]:
model.save('thisisatestmodel')


# 4. Train Model Using Curriculum


In [71]:
model.load("C:/Users/16132/Documents/ML-mario/Training/saved_models/Best_Model.zip")
# 1. Create the base environment
env = gym_super_mario_bros.make('SuperMarioBros-v0')
# 2. Simplify the controls 
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale, cuts down amount of data, as color data costs more, need to consider blue, red, green. Need to deal with only a third of the data now
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environment
env = DummyVecEnv([lambda: env])
# 5. Stack the frames: when frame stacking you get access not just to the current frame, but the most recent frames as well
env = VecFrameStack(env, 4, channels_order='last')
model.set_env(env)
model.learn(total_timesteps=3000000, callback=callback)

Wrapping the env in a VecTransposeImage.
Logging to C:/Users/16132/Documents/ML-mario/Training/logs/PPO_14
----------------------------
| time/              |     |
|    fps             | 165 |
|    iterations      | 1   |
|    time_elapsed    | 3   |
|    total_timesteps | 512 |
----------------------------
C:/Users/16132/Documents/ML-mario/Training/saved_models/\Best_Model
------------------------------------------
| time/                   |              |
|    fps                  | 67           |
|    iterations           | 2            |
|    time_elapsed         | 15           |
|    total_timesteps      | 1024         |
| train/                  |              |
|    approx_kl            | 0.0028126591 |
|    clip_fraction        | 0.0498       |
|    clip_range           | 0.2          |
|    entropy_loss         | -0.217       |
|    explained_variance   | 0.954        |
|    learning_rate        | 1e-06        |
|    loss                 | 20.4         |
|    n_updates      

KeyboardInterrupt: 

In [ ]:
model.load("C:/Users/16132/Documents/ML-mario/Training/saved_models/Best_Model.zip")
# 1. Create the base environment
env = gym_super_mario_bros.make('SuperMarioBros-1-3-v0')
# 2. Simplify the controls 
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale, cuts down amount of data, as color data costs more, need to consider blue, red, green. Need to deal with only a third of the data now
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environment
env = DummyVecEnv([lambda: env])
# 5. Stack the frames: when frame stacking you get access not just to the current frame, but the most recent frames as well
env = VecFrameStack(env, 4, channels_order='last')
model.set_env(env)
model.learn(total_timesteps=2000000, callback=callback)

Wrapping the env in a VecTransposeImage.
Logging to C:/Users/16132/Documents/ML-mario/Training/logs/PPO_18


C:\Users\16132\Documents\ML-mario\myenv\lib\site-packages\gym_super_mario_bros\smb_env.py:148: RuntimeWarning: overflow encountered in scalar subtract
  return (self.ram[0x86] - self.ram[0x071c]) % 256


----------------------------
| time/              |     |
|    fps             | 56  |
|    iterations      | 1   |
|    time_elapsed    | 9   |
|    total_timesteps | 512 |
----------------------------
-------------------------------------------
| time/                   |               |
|    fps                  | 47            |
|    iterations           | 2             |
|    time_elapsed         | 21            |
|    total_timesteps      | 1024          |
| train/                  |               |
|    approx_kl            | 1.0963064e-05 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.95         |
|    explained_variance   | 0.00569       |
|    learning_rate        | 1e-06         |
|    loss                 | 152           |
|    n_updates            | 10            |
|    policy_gradient_loss | -5.63e-05     |
|    value_loss           | 425           |
-------------------------------------------
-----

In [62]:
model.load("C:/Users/16132/Documents/ML-mario/Training/saved_models/Best_Model.zip")
# 1. Create the base environment
env = gym_super_mario_bros.make('SuperMarioBros-v2')
# 2. Simplify the controls 
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale, cuts down amount of data, as color data costs more, need to consider blue, red, green. Need to deal with only a third of the data now
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environment
env = DummyVecEnv([lambda: env])
# 5. Stack the frames: when frame stacking you get access not just to the current frame, but the most recent frames as well
env = VecFrameStack(env, 4, channels_order='last')
model.set_env(env)
model.learn(total_timesteps=2000000, callback=callback)

Wrapping the env in a VecTransposeImage.
Logging to C:/Users/16132/Documents/ML-mario/Training/logs/PPO_12
----------------------------
| time/              |     |
|    fps             | 138 |
|    iterations      | 1   |
|    time_elapsed    | 3   |
|    total_timesteps | 512 |
----------------------------
------------------------------------------
| time/                   |              |
|    fps                  | 80           |
|    iterations           | 2            |
|    time_elapsed         | 12           |
|    total_timesteps      | 1024         |
| train/                  |              |
|    approx_kl            | 9.778887e-09 |
|    clip_fraction        | 0            |
|    clip_range           | 0.2          |
|    entropy_loss         | -0.00142     |
|    explained_variance   | -0.798       |
|    learning_rate        | 1e-06        |
|    loss                 | 1e+03        |
|    n_updates            | 75090        |
|    policy_gradient_loss | -2.58e-05    |
| 

KeyboardInterrupt: 

In [ ]:
model.load("C:/Users/16132/Documents/ML-mario/Training/saved_models/Best_Model.zip")
# 1. Create the base environment
env = gym_super_mario_bros.make('SuperMarioBros-v3')
# 2. Simplify the controls 
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale, cuts down amount of data, as color data costs more, need to consider blue, red, green. Need to deal with only a third of the data now
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environment
env = DummyVecEnv([lambda: env])
# 5. Stack the frames: when frame stacking you get access not just to the current frame, but the most recent frames as well
env = VecFrameStack(env, 4, channels_order='last')
model.set_env(env)
model.learn(total_timesteps=2000000, callback=callback)

In [ ]:
model.load("C:/Users/16132/Documents/ML-mario/Training/saved_models/Best_Model.zip")
# 1. Create the base environment
env = gym_super_mario_bros.make('SuperMarioBros2-v0')
# 2. Simplify the controls 
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale, cuts down amount of data, as color data costs more, need to consider blue, red, green. Need to deal with only a third of the data now
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environment
env = DummyVecEnv([lambda: env])
# 5. Stack the frames: when frame stacking you get access not just to the current frame, but the most recent frames as well
env = VecFrameStack(env, 4, channels_order='last')
model.set_env(env)
model.learn(total_timesteps=2000000, callback=callback)

In [ ]:
model.load("C:/Users/16132/Documents/ML-mario/Training/saved_models/Best_Model.zip")
# 1. Create the base environment
env = gym_super_mario_bros.make('SuperMarioBros2-v1')
# 2. Simplify the controls 
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale, cuts down amount of data, as color data costs more, need to consider blue, red, green. Need to deal with only a third of the data now
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environment
env = DummyVecEnv([lambda: env])
# 5. Stack the frames: when frame stacking you get access not just to the current frame, but the most recent frames as well
env = VecFrameStack(env, 4, channels_order='last')
model.set_env(env)
model.learn(total_timesteps=2000000, callback=callback)

# 4. Test it Out


In [89]:
model = PPO.load("C:/Users/16132/Documents/ML-mario/Training/saved_models/Best_Model.zip")


In [90]:
# 1. Create the base environment
env = gym_super_mario_bros.make('SuperMarioBros-1-3-v0')
# 2. Simplify the controls 
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale, cuts down amount of data, as color data costs more, need to consider blue, red, green. Need to deal with only a third of the data now
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environment
env = DummyVecEnv([lambda: env])
# 5. Stack the frames: when frame stacking you get access not just to the current frame, but the most recent frames as well
env = VecFrameStack(env, 4, channels_order='last')
state = env.reset()


In [91]:
# Start the game 
state = env.reset()
# Loop through the game
while True: 
    
    action, _ = model.predict(state)
    state, reward, done, info = env.step(action)
    env.render()

KeyboardInterrupt: 

In [92]:
env.close()